In [ ]:
!pip install --upgrade datasets
!pip install -U accelerate
!pip install transformers
!pip install evaluate
!pip install datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 486.2/486.2 kB 17.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 13.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.5/212.5 kB 27.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.3/134.3 kB 18.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 32.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.6/227.6 kB 11.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.2/7.2 MB 84.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 72.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 40.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.4/81.4 kB 7.4 MB/s eta 0:00:00


In [ ]:
import evaluate
import numpy as np
from sklearn.metrics import precision_recall_fscore_support
import datasets
from datasets import load_dataset,load_metric
import re
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM, AutoModelForSequenceClassification,TrainingArguments, Trainer, EvalPrediction
from datasets import load_metric
from sklearn.metrics import accuracy_score, f1_score, recall_score
import torch

In [ ]:
#load dataset
ecthra = load_dataset("lex_glue", "ecthr_a")

Generating train split:   0%|          | 0/9000 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1000 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/1000 [00:00<?, ? examples/s]

Dataset lex_glue downloaded and prepared to /root/.cache/huggingface/datasets/lex_glue/ecthr_a/1.0.0/8a66420941bf6e77a7ddd4da4d3bfb7ba88ef48c1d55302a568ac650a095ca3a. Subsequent calls will reuse this data.


  0%|          | 0/3 [00:00<?, ?it/s]

In [ ]:
ecthra

DatasetDict({
    train: Dataset({
        features: ['text', 'labels'],
        num_rows: 9000
    })
    test: Dataset({
        features: ['text', 'labels'],
        num_rows: 1000
    })
    validation: Dataset({
        features: ['text', 'labels'],
        num_rows: 1000
    })
})

In [ ]:
# split train, validation & test data
train=ecthra['train']
validation=ecthra['validation']
test=ecthra['test']

In [ ]:
#check labels
dic = set()

for elem in validation["labels"]:
  for i in elem:
    if i not in dic:
      dic.add(i)
dic


{0, 1, 2, 3, 4, 5, 6, 7, 8, 9}

In [ ]:
#change labels into one hot encoding
num_classes = 10

def one_hot_encode_multi(labels, num_classes):
    encoded_labels = np.zeros((len(labels),num_classes), dtype=int)
    for i, sublist in enumerate(labels):
        encoded_labels[i, sublist] = 1
    return encoded_labels

In [ ]:
#train labels into one hot encodingg
train_one_hot=one_hot_encode_multi(train['labels'],10)
train_one_hot = train_one_hot.tolist()
train=train.add_column(name="labels_one_hot", column=train_one_hot)

In [ ]:
#test labels into one hot encodingg
test_one_hot=one_hot_encode_multi(test['labels'],10)
test_one_hot = test_one_hot.tolist()
test=test.add_column(name="labels_one_hot", column=test_one_hot)

In [ ]:
#validation labels into one hot encodingg
validation_one_hot=one_hot_encode_multi(validation['labels'],10)
validation_one_hot = validation_one_hot.tolist()
validation=validation.add_column(name="labels_one_hot", column=validation_one_hot)

In [ ]:
# re format the data to feed into the model
def format_text(text):
    text_format = []
    text = [[re.sub(r"^\d+\.\s*", "", s) for s in sublst] for sublst in text]
    for each in text:
        text_format.append(' '.join(each))
    prefix = 'judge the following case: '
    text_format = [prefix + s for s in text_format]
    return text_format

In [ ]:
train_text_format=format_text(train['text'])
train=train.remove_columns('text')
train=train.add_column(name="text", column=train_text_format)
ecthra['train']=train

In [ ]:
train_text_format

['judge the following case: At the beginning of the events relevant to the application, K. had a daughter, P., and a son, M., born in 1986 and 1988 respectively. P.’s father is X and M.’s father is V. From March to May 1989 K. was voluntarily hospitalised for about three months, having been diagnosed as suffering from schizophrenia. From August to November 1989 and from December 1989 to March 1990, she was again hospitalised for periods of about three months on account of this illness. In 1991 she was hospitalised for less than a week, diagnosed as suffering from an atypical and undefinable psychosis. It appears that social welfare and health authorities have been in contact with the family since 1989. The applicants initially cohabited from the summer of 1991 to July 1993. In 1991 both P. and M. were living with them. From 1991 to 1993 K. and X were involved in a custody and access dispute concerning P. In May 1992 a residence order was made transferring custody of P. to X. K. was aga

In [ ]:
len(train_text_format)

9000

In [ ]:
test_text_format=format_text(test['text'])
test=test.remove_columns('text')
test=test.add_column(name="text", column=test_text_format)
ecthra['test']=test

In [ ]:
validation_text_format=format_text(validation['text'])
validation=validation.remove_columns('text')
validation=validation.add_column(name="text", column=validation_text_format)
ecthra['validation']=validation

In [ ]:
ecthra=ecthra.remove_columns('labels')
ecthra=ecthra.rename_column('labels_one_hot', 'labels')

In [ ]:
ecthra["train"]

Dataset({
    features: ['labels', 'text'],
    num_rows: 9000
})

In [ ]:
#call the tokenizer
model_ckpt = "google/flan-t5-base"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt, problem_type="multi_label_classification")

In [ ]:
#tokenize the data
def tokenize_and_encode(examples):
  return tokenizer(examples["text"], truncation=True)

In [ ]:
cols = ecthra["train"].column_names
cols.remove("labels")
ds_enc = ecthra.map(tokenize_and_encode, batched=True, remove_columns=cols)
# ds_enc["train"]["attention_mask"]
# # ds_enc["test"]["input_ids"] = ds_enc["train"]["input_ids"].long()
# # ds_enc["validation"]["input_ids"] = ds_enc["train"]["input_ids"].long()
# # input_ids = dataset['train']['input_ids'].long()

Map:   0%|          | 0/9000 [00:00<?, ? examples/s]

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

In [ ]:
ds_enc

DatasetDict({
    train: Dataset({
        features: ['labels', 'input_ids', 'attention_mask'],
        num_rows: 9000
    })
    test: Dataset({
        features: ['labels', 'input_ids', 'attention_mask'],
        num_rows: 1000
    })
    validation: Dataset({
        features: ['labels', 'input_ids', 'attention_mask'],
        num_rows: 1000
    })
})

In [ ]:
len(ds_enc["train"]["labels"])

9000

In [ ]:
ds_enc.set_format("torch")

In [ ]:
#define the model
num_labels=10
model = AutoModelForSeq2SeqLM.from_pretrained(model_ckpt, num_labels=num_labels, problem_type="multi_label_classification")
# model = AutoModelForSeq2SeqLM.from_pretrained("google/flan-t5-base")

In [ ]:
model.to('cuda')

T5ForConditionalGeneration(
  (shared): Embedding(32128, 768)
  (encoder): T5Stack(
    (embed_tokens): Embedding(32128, 768)
    (block): ModuleList(
      (0): T5Block(
        (layer): ModuleList(
          (0): T5LayerSelfAttention(
            (SelfAttention): T5Attention(
              (q): Linear(in_features=768, out_features=768, bias=False)
              (k): Linear(in_features=768, out_features=768, bias=False)
              (v): Linear(in_features=768, out_features=768, bias=False)
              (o): Linear(in_features=768, out_features=768, bias=False)
              (relative_attention_bias): Embedding(32, 12)
            )
            (layer_norm): T5LayerNorm()
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (1): T5LayerFF(
            (DenseReluDense): T5DenseGatedActDense(
              (wi_0): Linear(in_features=768, out_features=2048, bias=False)
              (wi_1): Linear(in_features=768, out_features=2048, bias=False)
              (wo):

### **Run the two cells below: New Approach**

In [ ]:
#Calculate accuracy, recall, F1 score
from sklearn.metrics import f1_score, roc_auc_score, accuracy_score, recall_score
from transformers import EvalPrediction
import torch
import numpy as np

# source: https://jesusleal.io/2021/04/21/Longformer-multilabel-classification/
def multi_label_metrics(predictions, labels, threshold=0.5):
    # first, apply sigmoid on predictions which are of shape (batch_size, num_labels)

    # next, use threshold to turn them into integer predictions
    # y_pred = np.zeros(probs.shape, dtype=int)
    # y_pred[np.where(probs >= threshold)] = 1
    sigmoid = torch.nn.Sigmoid() #call sigmoid
    probs = np.argmax(predictions, axis=-1) #return an array of the same shape as predictions but reduced by one dimension, where each value is the index of the maximum value in that sub-array along the last dimension of predictions
    probss = sigmoid(torch.Tensor(probs))
    print("predictions: ", predictions)
    print("predictions size: ", predictions.shape)
    # probss = sigmoid(torch.Tensor(predictions))
    print("probss (after sigmoid): ", probss)
    # probss = np.round(probss)
    # print("probss (after round): ", probss)
    print("probss shape: ", probss.shape)
    y_pred = np.zeros(probss.shape)
    y_pred[np.where(probss >= threshold)] = 1

    # finally, compute metrics
    y_true = labels
    print("y_pred: ", y_pred)
    print("y_pred shape: ", y_pred.shape)
    print("y_true: ", y_true)
    print("y_true shape: ", y_true.shape)
    f1_micro_average = f1_score(y_true=y_true, y_pred=y_pred, average='micro')
    # print("f1 average: ", f1_micro_average)
    roc_auc = roc_auc_score(y_true, y_pred, average = 'micro')
    accuracy = accuracy_score(y_true, y_pred)
    recall = recall_score(y_true, y_pred, average='macro')
    # return as dictionary
    metrics = {'f1': f1_micro_average,
               'roc_auc': roc_auc,
               'accuracy': accuracy,
               'recall': recall}
    return metrics

def compute_metrics(p: EvalPrediction):
    preds = p.predictions[0]
    print("preds: ", preds)
    print("labels: ", p.label_ids)
    result = multi_label_metrics(
        predictions=preds,
        labels=p.label_ids)
    return result

In [ ]:
batch_size = 1
metric_name = "f1"

#define arguments, parameters such as learning rate and number of epochs, batch sizes
args = TrainingArguments(
    f"output",
    evaluation_strategy = "epoch",
    save_strategy = "epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=1,
    weight_decay=0.01,
    load_best_model_at_end=True,
    metric_for_best_model=metric_name,
)

# args = TrainingArguments(".",
#                          num_train_epochs=1,
#                          per_device_train_batch_size=1,
#                          per_device_eval_batch_size=1)


trainer = Trainer(model=model,
                  args=args,
                  train_dataset=ds_enc["train"],
                  eval_dataset=ds_enc["validation"],
                  tokenizer=tokenizer,
                  compute_metrics=compute_metrics)

In [ ]:
#evaluate the model before training
trainer.evaluate()

You're using a T5TokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


preds:  [[[-44.07717    -4.471682  -10.646845  ... -44.14505   -43.87517
   -44.26783  ]
  [-44.077187   -4.4716854 -10.646852  ... -44.145054  -43.875187
   -44.267838 ]
  [-44.07718    -4.4716825 -10.646847  ... -44.145042  -43.87517
   -44.26783  ]
  ...
  [-44.07718    -4.4716835 -10.646846  ... -44.14505   -43.875175
   -44.26783  ]
  [-44.07718    -4.4716835 -10.646848  ... -44.14505   -43.87518
   -44.267834 ]
  [-44.07718    -4.4716845 -10.646848  ... -44.145046  -43.875175
   -44.267838 ]]

 [[-45.866726   -1.9070461 -10.449186  ... -46.01428   -45.75518
   -46.223106 ]
  [-45.866714   -1.9070435 -10.4491825 ... -46.014267  -45.755165
   -46.22309  ]
  [-51.607967   -1.4488294  -9.836205  ... -51.508568  -51.4952
   -51.718605 ]
  ...
  [-45.814114   -2.4129062 -11.536377  ... -46.05879   -45.92122
   -46.242256 ]
  [-45.07319    -2.539969  -11.595425  ... -45.303223  -45.176613
   -45.499016 ]
  [-44.830322   -2.645534  -11.650363  ... -45.055267  -44.933403
   -45.25579  ]]


{'eval_loss': 43.360721588134766,
 'eval_f1': 0.19168173598553342,
 'eval_roc_auc': 0.5,
 'eval_accuracy': 0.0,
 'eval_recall': 1.0,
 'eval_runtime': 78.0856,
 'eval_samples_per_second': 12.806,
 'eval_steps_per_second': 12.806}

In [ ]:
#train the model
trainer.train()

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


preds:  [[[22.801128  20.130844   3.0313013 ... 13.48916   14.06292   13.566088 ]
  [22.801128  20.130844   3.0313013 ... 13.489162  14.062922  13.56609  ]
  [22.801128  20.130846   3.0313034 ... 13.489162  14.0629225 13.566089 ]
  ...
  [22.801125  20.130844   3.031302  ... 13.489157  14.062919  13.566083 ]
  [22.801126  20.130844   3.0313013 ... 13.48916   14.06292   13.566085 ]
  [22.801125  20.130844   3.031302  ... 13.48916   14.062918  13.566084 ]]

 [[21.7616    20.148403   2.4472995 ... 12.474999  13.014339  12.526709 ]
  [21.7616    20.1484     2.4472992 ... 12.474999  13.014341  12.526707 ]
  [26.230415  20.804722   0.5036174 ... 15.177634  15.289673  15.020848 ]
  ...
  [33.720963  24.254787   5.676408  ... 21.985575  22.640621  22.095633 ]
  [32.944393  23.94854    5.5142198 ... 21.386272  22.034628  21.494986 ]
  [32.27045   23.699152   5.3801336 ... 20.856503  21.500216  20.964127 ]]

 [[21.159431  19.95669    2.5774918 ... 11.986431  12.544032  12.066063 ]
  [21.159428  

TrainOutput(global_step=9000, training_loss=1.1420637834337022, metrics={'train_runtime': 2215.457, 'train_samples_per_second': 4.062, 'train_steps_per_second': 4.062, 'total_flos': 5821128940243968.0, 'train_loss': 1.1420637834337022, 'epoch': 1.0})

In [ ]:
#evaluate the model after training
trainer.evaluate()

preds:  [[[22.801128  20.130844   3.0313013 ... 13.48916   14.06292   13.566088 ]
  [22.801128  20.130844   3.0313013 ... 13.489162  14.062922  13.56609  ]
  [22.801128  20.130846   3.0313034 ... 13.489162  14.0629225 13.566089 ]
  ...
  [22.801125  20.130844   3.031302  ... 13.489157  14.062919  13.566083 ]
  [22.801126  20.130844   3.0313013 ... 13.48916   14.06292   13.566085 ]
  [22.801125  20.130844   3.031302  ... 13.48916   14.062918  13.566084 ]]

 [[21.7616    20.148403   2.4472995 ... 12.474999  13.014339  12.526709 ]
  [21.7616    20.1484     2.4472992 ... 12.474999  13.014341  12.526707 ]
  [26.230415  20.804722   0.5036174 ... 15.177634  15.289673  15.020848 ]
  ...
  [33.720963  24.254787   5.676408  ... 21.985575  22.640621  22.095633 ]
  [32.944393  23.94854    5.5142198 ... 21.386272  22.034628  21.494986 ]
  [32.27045   23.699152   5.3801336 ... 20.856503  21.500216  20.964127 ]]

 [[21.159431  19.95669    2.5774918 ... 11.986431  12.544032  12.066063 ]
  [21.159428  

{'eval_loss': 0.3782864511013031,
 'eval_f1': 0.19168173598553342,
 'eval_roc_auc': 0.5,
 'eval_accuracy': 0.0,
 'eval_recall': 1.0,
 'eval_runtime': 74.0093,
 'eval_samples_per_second': 13.512,
 'eval_steps_per_second': 13.512,
 'epoch': 1.0}

# **Cells Below are for Experiments**

# **Experiment 1**

In [ ]:
from sklearn.metrics import f1_score, roc_auc_score, accuracy_score, recall_score
from transformers import EvalPrediction
import torch
import numpy as np

# source: https://jesusleal.io/2021/04/21/Longformer-multilabel-classification/
def multi_label_metrics(predictions, labels, threshold=0.5):
    # first, apply sigmoid on predictions which are of shape (batch_size, num_labels)

    # next, use threshold to turn them into integer predictions
    # y_pred = np.zeros(probs.shape, dtype=int)
    # y_pred[np.where(probs >= threshold)] = 1
    sigmoid = torch.nn.Sigmoid() #call sigmoid
    # probs = np.argmax(predictions, axis=-1) #return an array of the same shape as predictions but reduced by one dimension, where each value is the index of the maximum value in that sub-array along the last dimension of predictions
    # probss = sigmoid(torch.Tensor(probs))
    print("predictions: ", predictions)
    print("predictions size: ", predictions.shape)
    probss = sigmoid(torch.Tensor(predictions))
    print("probss (after sigmoid): ", probss)
    probss = np.round(probss)
    print("probss (after round): ", probss)
    print("probss shape: ", probss.shape)
    y_pred = np.zeros(probss.shape)
    y_pred[np.where(probss >= threshold)] = 1

    # finally, compute metrics
    y_true = labels
    print("y_pred: ", y_pred)
    print("y_pred shape: ", y_pred.shape)
    print("y_true: ", y_true)
    print("y_true shape: ", y_true.shape)
    f1_micro_average = f1_score(y_true=y_true, y_pred=y_pred, average='micro')
    # print("f1 average: ", f1_micro_average)
    roc_auc = roc_auc_score(y_true, y_pred, average = 'micro')
    accuracy = accuracy_score(y_true, y_pred)
    recall = recall_score(y_true, y_pred, average='macro')
    # return as dictionary
    metrics = {'f1': f1_micro_average,
               'roc_auc': roc_auc,
               'accuracy': accuracy,
               'recall': recall}
    return metrics

def compute_metrics(p: EvalPrediction):
    preds = p.predictions[0]
    print("preds: ", preds)
    print("labels: ", p.label_ids)
    result = multi_label_metrics(
        predictions=preds,
        labels=p.label_ids)
    return result



batch_size = 1
metric_name = "f1"

args = TrainingArguments(
    f"output",
    evaluation_strategy = "epoch",
    save_strategy = "epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=1,
    weight_decay=0.01,
    load_best_model_at_end=True,
    metric_for_best_model=metric_name,
)

# args = TrainingArguments(".",
#                          num_train_epochs=1,
#                          per_device_train_batch_size=1,
#                          per_device_eval_batch_size=1)


trainer = Trainer(model=model,
                  args=args,
                  train_dataset=ds_enc["train"],
                  eval_dataset=ds_enc["validation"],
                  tokenizer=tokenizer,
                  compute_metrics=compute_metrics)

In [ ]:
trainer.evaluate()

preds:  [[[22.801128  20.130844   3.0313013 ... 13.48916   14.06292   13.566088 ]
  [22.801128  20.130844   3.0313013 ... 13.489162  14.062922  13.56609  ]
  [22.801128  20.130846   3.0313034 ... 13.489162  14.0629225 13.566089 ]
  ...
  [22.801125  20.130844   3.031302  ... 13.489157  14.062919  13.566083 ]
  [22.801126  20.130844   3.0313013 ... 13.48916   14.06292   13.566085 ]
  [22.801125  20.130844   3.031302  ... 13.48916   14.062918  13.566084 ]]

 [[21.7616    20.148403   2.4472995 ... 12.474999  13.014339  12.526709 ]
  [21.7616    20.1484     2.4472992 ... 12.474999  13.014341  12.526707 ]
  [26.230415  20.804722   0.5036174 ... 15.177634  15.289673  15.020848 ]
  ...
  [33.720963  24.254787   5.676408  ... 21.985575  22.640621  22.095633 ]
  [32.944393  23.94854    5.5142198 ... 21.386272  22.034628  21.494986 ]
  [32.27045   23.699152   5.3801336 ... 20.856503  21.500216  20.964127 ]]

 [[21.159431  19.95669    2.5774918 ... 11.986431  12.544032  12.066063 ]
  [21.159428  

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <cell line: 1>:1                                                                              │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/transformers/trainer.py:3053 in evaluate                 │
│                                                                                                  │
│   3050 │   │   start_time = time.time()                                                          │
│   3051 │   │                                                                                     │
│   3052 │   │   eval_loop = self.prediction_loop if self.args.use_legacy_prediction_loop else se  │
│ ❱ 3053 │   │   output = eval_loop(                                                               │
│   3054 │   │   │   eval_dataloader,                                                              │
│   3055 │   │   │   description="Evaluation",                                                     │
│   3056 │   │   │   # No point gathering the predictions if there are no metrics, otherwise we d  │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/transformers/trainer.py:3353 in evaluation_loop          │
│                                                                                                  │
│   3350 │   │   │   │   │   EvalPrediction(predictions=all_preds, label_ids=all_labels, inputs=a  │
│   3351 │   │   │   │   )                                                                         │
│   3352 │   │   │   else:                                                                         │
│ ❱ 3353 │   │   │   │   metrics = self.compute_metrics(EvalPrediction(predictions=all_preds, lab  │
│   3354 │   │   else:                                                                             │
│   3355 │   │   │   metrics = {}                                                                  │
│   3356                                                                                           │
│ in compute_metrics:48                                                                            │
│ in multi_label_metrics:32                                                                        │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1146 in f1_score      │
│                                                                                                  │
│   1143 │   >>> f1_score(y_true, y_pred, average=None)                                            │
│   1144 │   array([0.66666667, 1.        , 0.66666667])                                           │
│   1145 │   """                                                                                   │
│ ❱ 1146 │   return fbeta_score(                                                                   │
│   1147 │   │   y_true,                                                                           │
│   1148 │   │   y_pred,                                                                           │
│   1149 │   │   beta=1,                                                                           │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1287 in fbeta_score   │
│                                                                                                  │
│   1284 │   array([0.71..., 0.        , 0.        ])                                              │
│   1285 │   """                                                                                   │
│   1286 │                                                   

# **Experiment**

In [ ]:
args = TrainingArguments(".",
                         num_train_epochs=1,
                         per_device_train_batch_size=1,
                         per_device_eval_batch_size=1)


trainer = Trainer(model=model,
                  args=args,
                  train_dataset=ds_enc["train"],
                  eval_dataset=ds_enc["validation"],
                  tokenizer=tokenizer)

In [ ]:
predictions = trainer.predict(ds_enc["validation"])
# print(predictions.predictions.shape, predictions.label_ids.shape)
print(predictions)


In [ ]:
predictions.predictions[0]

In [ ]:
predictions.predictions[1].shape

In [ ]:
predictions.predictions[1]

In [ ]:
print(predictions[0][0]) #shape: (1000, 10, 32128)

In [ ]:
ls = np.argmax(predictions[0][0], axis=-1)
ls.shape

In [ ]:
ls

In [ ]:
print("predictions: ", predictions.predictions[0].shape)
print("labels: ", predictions.label_ids.shape)
# print("label_ids: ", predictions.label_ids)
print("(408, 2) (408,)")
# len()

In [ ]:
len(predictions.predictions[0])

In [ ]:
import numpy as np

preds = np.argmax(predictions.predictions[0], axis=-1)
# preds.shape
preds

In [ ]:
predictions.predictions[0]

In [ ]:
preds

In [ ]:
sigmoid = torch.nn.Sigmoid()
probs = sigmoid(torch.Tensor(preds))
probs

In [ ]:
for elem in probs:
  print(elem)

In [ ]:
probs.shape
probs[np.where(probs >= 0.5)] = 1

In [ ]:
probs

In [ ]:
ds_enc["train"]['labels'].shape #[9000, 10]

In [ ]:
len(ds_enc["train"]['input_ids']) #9000

In [ ]:
ds_enc["train"]['input_ids'][0].shape #512

In [ ]:
predictions = trainer.predict(ds_enc["validation"])
print(predictions.predictions.shape, predictions.label_ids.shape)

# import numpy as np
# preds = np.argmax(predictions.predictions, axis=-1)

# import evaluate

# metric = evaluate.load("lex_glue", "ecthr_b")
# metric.compute(predictions=preds, references=predictions.label_ids)

In [ ]:
ds_enc["validation"]

In [ ]:
trainer.evaluate()

In [ ]:
trainer.train()

In [ ]:
trainer.evaluate()

print arrucacy (evaluation , train, test)
confusion matrix
change hyper parameters(batch size, LR, etc)
run test data with different checkpoints